In [53]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import seaborn as sns
import optuna
import datetime
import joblib
from scipy.stats import pearsonr
from utils import Country_temperature

from xgboost import XGBRegressor
from sklearn.metrics import mean_squared_error
from sklearn.decomposition import PCA
color_pal = sns.color_palette()
pd.options.plotting.backend = "plotly"
plt.style.use('fivethirtyeight')

# HR prediction in France

## Data processing

### HR data

In [54]:
HRE = pd.read_csv('./data_input/HRE_tab.csv')
HRE.index = pd.to_datetime(HRE[['Year','Month','Day']])

### TP data

In [55]:
# Precipitation
TP = pd.read_csv("./data_input/TP_tab.csv")
TP.index = pd.to_datetime(TP[['Year','Month','Day']])
TP.drop(['Year','Month','Day'],axis=1,inplace=True)

In [56]:
n1 = 30
TP_cum_month = TP.rolling(n1).sum()
TP_cum_month.iloc[:n1-1] = TP.iloc[:n1-1].cumsum()

In [57]:
n2 = 7
TP_cum_7d = TP.rolling(n2).sum()
TP_cum_7d.iloc[:n2-1] = TP.iloc[:n2-1].cumsum()

In [78]:
TP[Country_temperature(TP,'FR')].plot()

In [59]:
# delay of 30 day
TP_cum_month_delayed = TP_cum_month.shift(periods=1, freq='30d').add_suffix('_delayed')
TP_cum_month_delayed[Country_temperature(TP_cum_month_delayed,'FR')].plot()

In [60]:
# Temperature
TA = pd.read_csv("./data_input/TA_tab.csv")
TA.index = pd.to_datetime(TA[['Year','Month','Day']])
TA.drop(['Year','Month','Day'],axis=1,inplace=True)

### Features

In [61]:
from utils import temperature_pca

Features creation

In [79]:
# Time Features
Features = HRE[[]].copy()
# Features['quarter'] = Features.index.quarter
# Features['month'] = Features.index.month
Features['dayofyear'] = Features.index.dayofyear
Features['dayofweek'] = Features.index.dayofweek
Features['weekofyear'] = Features.index.isocalendar().week.astype("int64")
# # Precipitation PCA on all location features
# Features = Features.merge(
#     temperature_pca(TP_cum_3d,0.95,'FR',prefix='TP_cum_3d'),
#     how='left',
#     left_index=True,
#     right_index=True
#     )
# Precipitation PCA on all location features
Features = Features.merge(
    temperature_pca(TA,1,'all',prefix='TA'),
    how='left',
    left_index=True,
    right_index=True
    )
Features = Features.merge(
    temperature_pca(TA,1,'FR',prefix='TA'),
    how='left',
    left_index=True,
    right_index=True
    )
Features = Features.merge(
    temperature_pca(TP_cum_month,0.95,'all',prefix='TP_cum_month'),
    how='left',
    left_index=True,
    right_index=True
    )
Features = Features.merge(
    temperature_pca(TP_cum_month_delayed,0.95,'all',prefix='TP_cum_month_delayed'),
    how='left',
    left_index=True,
    right_index=True
    )
Features = Features.merge(
    temperature_pca(TP_cum_7d,0.95,'all',prefix='TP_cum_7d'),
    how='left',
    left_index=True,
    right_index=True
    )
print(f"{Features.shape[1]} Features : {Features.columns.to_list()}")

127 Features : ['dayofyear', 'dayofweek', 'weekofyear', 'TA_all_PCA_1', 'TA_FR_PCA_1', 'TP_cum_month_all_PCA_1', 'TP_cum_month_all_PCA_2', 'TP_cum_month_all_PCA_3', 'TP_cum_month_all_PCA_4', 'TP_cum_month_all_PCA_5', 'TP_cum_month_all_PCA_6', 'TP_cum_month_all_PCA_7', 'TP_cum_month_all_PCA_8', 'TP_cum_month_all_PCA_9', 'TP_cum_month_all_PCA_10', 'TP_cum_month_all_PCA_11', 'TP_cum_month_all_PCA_12', 'TP_cum_month_all_PCA_13', 'TP_cum_month_all_PCA_14', 'TP_cum_month_all_PCA_15', 'TP_cum_month_all_PCA_16', 'TP_cum_month_all_PCA_17', 'TP_cum_month_all_PCA_18', 'TP_cum_month_all_PCA_19', 'TP_cum_month_all_PCA_20', 'TP_cum_month_all_PCA_21', 'TP_cum_month_all_PCA_22', 'TP_cum_month_all_PCA_23', 'TP_cum_month_all_PCA_24', 'TP_cum_month_all_PCA_25', 'TP_cum_month_all_PCA_26', 'TP_cum_month_all_PCA_27', 'TP_cum_month_all_PCA_28', 'TP_cum_month_all_PCA_29', 'TP_cum_month_all_PCA_30', 'TP_cum_month_all_PCA_31', 'TP_cum_month_delayed_all_PCA_1', 'TP_cum_month_delayed_all_PCA_2', 'TP_cum_month_del

In [80]:
X_train = Features.query('index >= 2015&index < 2019')
y_train = HRE[['FR']].query('index >= 2015&index < 2019')

X_test = Features.query('index >= 2019&index < "2020-03-01"')
y_test = HRE[['FR']].query('index >= 2019&index < "2020-03-01"')

X_validation =Features.query('index >= "2020-03-01"')
y_validation = HRE[['FR']].query('index >= "2020-03-01"')

In [81]:
study = optuna.create_study(direction='minimize', study_name="HRE-experiment")

[I 2022-12-30 00:15:59,996] A new study created in memory with name: HRE-experiment


In [82]:
def objective(trial):
    params = {
        'learning_rate' : trial.suggest_float('learning_rate', 1e-5, 1e-2),
        'n_estimators' : trial.suggest_int('n_estimators', 500, 2500),
        'max_depth' : trial.suggest_int('max_depth', 2, 25),
        'importance_type' : trial.suggest_categorical('importance_type', ['weight', 'gain', 'cover']),
        'reg_lambda' : trial.suggest_float('lambda', 1e-8, 1.0),
        'reg_alpha' : trial.suggest_float('alpha', 1e-8, 1.0)
    }

    # Create an XGBRegressor model with the sampled hyperparameters
    model = XGBRegressor(**params)
    
    # Fit the model on the training data
    model.fit(X_train, y_train)
    
    # Calculate the mean squared error on the validation set
    mse = mean_squared_error(y_test, model.predict(X_test))
    
    # Return the negative MSE to minimize the objective
    return mse

In [83]:
# Get the current date and time
now = datetime.datetime.now()
# Format the current date and time as a string without the seconds
now_str = now.strftime("%Y-%m-%d %H_%M")
n_trials = 100
study = optuna.create_study(direction='minimize',study_name=now_str+f'--{n_trials}')

[I 2022-12-30 00:16:00,116] A new study created in memory with name: 2022-12-30 00_16--100


In [84]:
study.optimize(objective, n_trials=n_trials)

[I 2022-12-30 00:16:02,932] Trial 0 finished with value: 0.00642052581632493 and parameters: {'learning_rate': 0.005895348933276252, 'n_estimators': 603, 'max_depth': 4, 'importance_type': 'gain', 'lambda': 0.7102071673872395, 'alpha': 0.21240197520976423}. Best is trial 0 with value: 0.00642052581632493.
[I 2022-12-30 00:16:17,168] Trial 1 finished with value: 0.006809133365044528 and parameters: {'learning_rate': 0.0060346330010139565, 'n_estimators': 1663, 'max_depth': 7, 'importance_type': 'gain', 'lambda': 0.33832840132017244, 'alpha': 0.8725861100428116}. Best is trial 0 with value: 0.00642052581632493.
[I 2022-12-30 00:16:58,374] Trial 2 finished with value: 0.007884015425431039 and parameters: {'learning_rate': 0.004270025747935724, 'n_estimators': 1650, 'max_depth': 24, 'importance_type': 'cover', 'lambda': 0.6619447121296893, 'alpha': 0.9307903534828241}. Best is trial 0 with value: 0.00642052581632493.
[I 2022-12-30 00:17:03,872] Trial 3 finished with value: 0.08221523729907

In [85]:
# Get the current date and time
now = datetime.datetime.now()
# Format the current date and time as a string without the seconds
now_str = now.strftime("%Y-%m-%d %H_%M")
joblib.dump(study, f"./OPTUNA_results/{now_str}--{n_trials}.pkl")

['./OPTUNA_results/2022-12-30 00_38--100.pkl']

In [86]:
best_params = study.best_params
model = XGBRegressor(**best_params)
model.fit(X_train,y_train)

# Evaluate the model on the test set
test_mse = mean_squared_error(y_test, model.predict(X_test))
print(f'Test MSE: {test_mse:.5f}')
print(f'Test RMSE: {np.sqrt(test_mse):.5f}')
print(f'Test R: {pearsonr(y_test.to_numpy().reshape(-1), model.predict(X_test))[0]:.3f}')
print(f"params = {best_params}")

Test MSE: 0.00557
Test RMSE: 0.07465
Test R: 0.714
params = {'learning_rate': 0.007798999304724741, 'n_estimators': 1337, 'max_depth': 3, 'importance_type': 'cover', 'lambda': 0.7236596366218204, 'alpha': 0.5596771113049114}


In [87]:
from utils import features_importance
features_importance(model)

In [88]:
y_predict = model.predict(X_test)
y_predict_val = model.predict(X_validation)
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x = HRE.index,
        y = HRE.FR,
        name = 'Truth Data'
    )
)
fig.add_trace(
    go.Scatter(
        x = X_test.index,
        y = y_predict,
        name = 'Test'
    )
)
fig.add_trace(
    go.Scatter(
        x = X_validation.index,
        y = y_predict_val,
        name = 'Validation'
    )
)
fig.update_layout(
    title = f"RMSE for test forecast : {np.round(np.sqrt(mean_squared_error(y_test,y_predict)),5)} | RMSE for validation forecast : {np.round(np.sqrt(mean_squared_error(y_validation,y_predict_val)),5)}",
    hovermode='x'
)

In [89]:
fig = optuna.visualization.plot_optimization_history(study)
fig.update_layout(hovermode='x')
fig.update_yaxes(type="log")
fig.show()

In [90]:
optuna.visualization.plot_param_importances(study)

In [91]:
fig = optuna.visualization.plot_slice(study)
fig.update_yaxes(type="log")
fig.show()
